# Page rank

In [32]:
import networkx as nx
import numpy as np
from typing import Tuple
from scipy.sparse import csr_matrix
from scipy import sparse
from scipy.sparse.linalg import eigs, norm

## Zadanie 1 Prosty ranking wierzchołków

In [85]:
graph = nx.DiGraph()

with open("data/Slashdot0811.txt") as file:
    nodes_count: int = int(file.readline())
    
    graph.add_nodes_from(range(nodes_count))
    
    lines = file.readlines()
    for line in lines:
        from_node: int
        to_node: int
        
        from_node, to_node = tuple(map(int, line.split("\t")))
        graph.add_edge(from_node, to_node)


raw_adj_matrix = nx.to_scipy_sparse_matrix(graph, dtype=float)

In [86]:
output_sums = np.ravel(raw_adj_matrix.sum(axis = 1))
quotients = np.zeros(output_sums.shape[0])
quotients[np.where(output_sums != 0)] = 1 / output_sums[np.where(output_sums != 0)]

adj_matrix = sparse.csr_matrix(sparse.spdiags(quotients, 0, *adj_matrix.get_shape())) @ adj_matrix

In [124]:
# power iterations method
def dominant_eigenvalue_eigenvector(A, G, max_iter: int = 1000, epsilon: float = 10**-14) -> Tuple[np.float64, np.ndarray]:
    n: int = A.get_shape()[0]
    result: np.ndarray = np.ones(n)
    prev_result:np.ndarray = np.zeros(n)
    dominant_eigenvalue: float = 0
        
    iter_count = 0
    while iter_count < max_iter and np.linalg.norm(prev_result - result) > epsilon:
        prev_result = result
        result = result @ A
        dominant_eigenvalue = np.abs(sparse.find(result)[2]).max()
        result = result / dominant_eigenvalue
        iter_count += 1 
        
    return dict(zip(list(G), map(float, result)))

In [125]:
custom_pagerank = dominant_eigenvalue_eigenvector(adj_matrix, graph)

In [126]:
lib_pagerank = nx.pagerank(graph)

In [127]:
# some error in code probably :/
for el1, el2 in [ tuple([custom_pagerank[i], lib_pagerank[i]]) for i in custom_pagerank.keys()]:
    print(el1, el2)

0.00014146212863950705 0.0001784471251795752
9.10456948536203e-05 9.82354842394754e-05
3.5215299779878046e-05 3.5294288543868755e-05
7.040211158205087e-05 7.944147299221839e-05
6.223567888438487e-05 7.16916429079427e-05
3.7375523583115605e-06 7.056331940857706e-06
5.988464210767397e-05 6.710372514979558e-05
1.4689871830151125e-05 2.05819785531596e-05
0.00021658533890753313 0.00022648446678898572
3.7852778186811392e-06 9.555011146194654e-06
3.395880574484205e-05 4.0626049225873195e-05
1.945950195832622e-05 2.921943424802018e-05
4.345137485278192e-05 5.7577387020891234e-05
5.7115354942031785e-05 7.112815808882015e-05
9.782526113128197e-05 0.00011703728383908945
0.000351258708656761 0.0004938977049512389
1.0489226614278557e-05 1.5269928612590688e-05
0.00011379904706821589 0.00012149823469656375
1.2675115821748256e-05 2.1181024681375094e-05
6.642276246286278e-05 6.97597948022706e-05
0.00010014940432549779 0.00011364069457463572
2.660299826059398e-05 3.281564720529894e-05
0.0001498335903979

8.512945361562896e-06 1.1674108011935452e-05
2.3840230984177402e-06 6.635124200385353e-06
2.9536629484905207e-05 4.36403287798792e-05
6.332299452089247e-05 7.578260033072095e-05
1.379429072104213e-05 2.2127160365626784e-05
1.6757661815618983e-05 2.141627227299758e-05
3.000592447398155e-06 5.671732161064976e-06
1.1734921450075387e-05 1.624324722823117e-05
1.2882913300527044e-06 5.38239995156553e-06
5.962918848289291e-06 9.39423777132785e-06
1.2882913300527044e-06 5.38239995156553e-06
1.9679334650894386e-06 1.000215638713706e-05
2.8350190443929938e-05 4.098444395456299e-05
3.49973696209732e-05 4.484743908268087e-05
2.3578178953555408e-05 3.1923874202755845e-05
4.9811728258934346e-05 4.160192859108422e-05
1.9316301906794817e-06 4.9604862936885644e-06
3.6138378582541454e-06 6.563286930801709e-06
4.352564128521791e-05 5.5877829107442994e-05
2.1711209209141404e-05 3.234785255077981e-05
0.00012060711920075881 0.00010033097937395053
3.035028705028009e-05 3.7998805890995976e-05
2.72706657629070

1.2283257104407657e-06 5.686389559280653e-06
4.167191748142552e-06 9.23208172500174e-06
1.2283257104407657e-06 5.686389559280653e-06
2.2503445738032108e-05 3.21769871234658e-05
1.2283257104407657e-06 5.686389559280653e-06
5.529690943883974e-06 8.21013496381672e-06
6.22956810917865e-06 8.680962241779495e-06
4.748518489785498e-06 9.370739256618679e-06
0.00012506843932048238 0.00014716371999525261
1.9304501038490946e-05 2.3088955289766917e-05
1.2283257104407657e-06 5.686389559280653e-06
1.2283257104407657e-06 5.686389559280653e-06
2.2329735151605108e-05 3.365437332247127e-05
5.949368903327318e-06 1.5021305076495212e-05
3.1993615705456137e-06 5.952961481617432e-06
2.740661363448569e-05 3.762548324482576e-05
5.457048620913622e-06 7.6895529917102e-06
5.032304875900833e-06 7.761714966694263e-06
3.241496256163783e-06 6.42958829987499e-06
2.689791786659094e-06 7.638562298742548e-06
9.307924761166757e-07 3.366784455952784e-06
1.2283257104407657e-06 5.686389559280653e-06
5.716991966136472e-06 9.1

5.259642328442988e-05 5.962985882466104e-05
3.5306912273817806e-06 1.128665120282266e-05
1.7668374846742616e-05 2.2380364188351767e-05
1.4981084816154038e-06 6.03790454625338e-06
7.588671727548065e-06 1.0338732800219624e-05
4.999019551943884e-06 7.727858913528604e-06
1.4981084816154038e-06 6.03790454625338e-06
2.5934799496977174e-06 6.144160516661375e-06
4.979061621361683e-06 1.074822057411173e-05
1.4981084816154038e-06 6.03790454625338e-06
2.1393670490961465e-05 2.9066428452710193e-05
2.5937815458260404e-06 6.226841544366845e-06
3.1571104047509877e-06 6.2670987425134735e-06
3.912212050783449e-06 7.415897601479205e-06
1.4695632240013954e-05 2.1078405971955564e-05
2.0637539262715405e-06 5.521732339204393e-06
1.683190245556312e-05 2.8623153272069956e-05
9.156793221355919e-06 1.301447966584555e-05
2.7550979031180677e-06 7.868347345673757e-06
1.4981084816154038e-06 6.03790454625338e-06
1.966826255022747e-06 6.518180856367452e-06
1.4981084816154038e-06 6.03790454625338e-06
1.424143389763007

4.757640110056884e-05 6.889306555389908e-05
8.739910087049223e-06 1.3397676953956782e-05
5.397038848585975e-06 8.795809011006445e-06
2.9688935678071992e-06 5.672172299774733e-06
3.5848520080074845e-05 4.4534443303785916e-05
2.911577216412538e-05 5.283708953992334e-05
2.8580207618448378e-05 3.464795501593732e-05
0.1307636361544177 1.97292498740824e-05
1.1600258877768319e-05 1.6685277719656788e-05
3.6429131924275834e-06 7.724252752726429e-06
1.151169506202716e-05 1.7045367421525097e-05
1.5031472322997564e-05 1.9095674507752565e-05
7.805734584509176e-07 4.895943647935909e-06
3.746015719003841e-05 5.0608910359639046e-05
3.081852281669736e-05 3.9805114603631675e-05
4.5102455912960875e-06 7.171230767881405e-06
4.8726208753310164e-05 5.400642222648906e-05
0.00014818425854109976 0.00017850068997258254
2.9587903089591136e-06 5.700788380856101e-06
5.0754794180672894e-05 6.876296815494303e-05
5.1197101571080497e-05 5.576036628689532e-05
1.08787408996236e-05 1.5481598049113497e-05
6.33310059336838

...

2.2733955630699414e-06 5.662037197512445e-06
1.3847295962987793e-06 5.264891621603855e-06
2.4408652089697255e-06 6.734398585106837e-06
1.2990357854128344e-06 6.563219031944249e-06
1.147607771496615e-06 9.126877011780163e-06
1.6728970058580064e-06 1.0355034871561053e-05
1.824060395720281e-06 6.256560155574315e-06
1.824060395720281e-06 6.256560155574315e-06
1.2434363828983365e-06 5.022251630561475e-06
1.2434363828983365e-06 5.022251630561475e-06
1.6077978761528882e-06 6.294498879119297e-06
1.3572337480624006e-06 5.972738060421889e-06
1.6694841117993163e-06 6.469894767276497e-06
1.334393792907472e-06 5.410067794195964e-06
1.3527924837141404e-06 4.98274590958012e-06
2.638014136425887e-06 7.833624274343204e-06
7.044939829441229e-07 5.408902944462802e-06
7.044939829441229e-07 5.408902944462802e-06
1.1453460899992402e-06 6.1804305438800855e-06
1.1453460899992402e-06 6.1804305438800855e-06
1.3260797378909194e-06 5.19297285503889e-06
0.004998174723145462 1.405967015180484e-05
0.0235302007534495

0.013813547448801292 1.3521753421719788e-05
0.013813547448801292 1.3521753421719788e-05
2.645993598457485e-06 1.0072071519280962e-05
1.5876462795345522e-06 6.249222297473768e-06
1.5360958671744667e-06 7.908735709018964e-06
1.5360958671744667e-06 7.908735709018964e-06
8.300627323879534e-07 5.345649972397875e-06
8.300627323879534e-07 5.345649972397875e-06
1.2894778250076356e-06 6.5304610265596426e-06
1.9808613745165205e-06 1.0157366729814945e-05
1.5025538109994667e-06 5.9257572533730205e-06
1.374531705999458e-06 6.75090255439215e-06
1.374531705999458e-06 6.75090255439215e-06
3.201689492099081e-06 9.841673355869914e-06
3.4593235295451663e-06 1.0243534756510693e-05
1.0641534911698886e-06 5.898658227191411e-06
3.4593235295451663e-06 1.0243534756510693e-05
1.805493445157067e-06 6.350885705672889e-06
6.936050354832499e-07 4.038068953215809e-06
0.06219724443835461 1.6389459429290183e-05
8.172561506485757e-07 7.644531319132564e-06
8.952750477844569e-07 4.235742476690477e-06
1.315362192918391e-0

0.00655907823378775 1.3032709502916357e-05
0.01917425087877982 2.2159486765586303e-05
1.2015515180526134e-06 5.8269195868426374e-06
1.2015515180526134e-06 5.8269195868426374e-06
4.716847691278704e-06 1.099184940826535e-05
3.6692096280821607e-06 9.14014908036854e-06
5.639589394392866e-06 1.2991372850704157e-05
9.953306260970509e-07 5.707180780862009e-06
1.0181936174995011e-06 5.492314911382337e-06
1.0181936174995011e-06 5.492314911382337e-06
1.5553448564419365e-06 1.0149028681046247e-05
5.456796078952956e-06 9.792868855229331e-06
1.193408593322835e-06 5.806164634798597e-06
1.7010799712721131e-06 6.826125209872217e-06
1.3480333360192e-06 6.1768905246098265e-06
1.3480333360192e-06 6.1768905246098265e-06
1.2677785516702417e-06 9.189528773769399e-06
1.1190787059033727e-06 9.251420165508299e-06
3.3753158631523445e-06 9.614731071001755e-06
0.01821572704933272 1.3459917709023882e-05
8.564219931898013e-07 7.102717145554701e-06
1.558416276805983e-06 8.518877924905138e-06
1.73661731311021e-06 7.1

1.810847509986376e-06 9.222435641047148e-06
1.2007869513674569e-06 6.107480520142717e-06
1.608807620371637e-06 7.526601471891106e-06
1.608807620371637e-06 7.526601471891106e-06
9.916363281343441e-07 5.503423101150142e-06
6.251144723967914e-07 5.80521392246526e-06
1.2246091634656201e-06 9.128396857884606e-06
1.2246091634656201e-06 9.128396857884606e-06
0.029788742702929638 1.810249533122e-05
1.201702868065666e-06 9.040666391028527e-06
1.0890978678275648e-06 6.383941428842578e-06
1.6705506538491162e-06 7.251272566949055e-06
1.1169906423185295e-06 5.967742508074938e-06
6.804295476874459e-07 3.97033832227667e-06
1.0935578202360603e-06 6.250896252879212e-06
1.6704676809181477e-06 1.079179225587767e-05
1.3119868081862093e-06 6.8652692113387915e-06
1.5401327535962557e-06 6.640884700550428e-06
1.2165510702104901e-06 9.00191707506239e-06
1.4757123446013832e-06 1.0876588190634701e-05
1.4757123446013832e-06 1.0876588190634701e-05
1.3630235405042042e-06 6.867634833855815e-06
3.243923173719053e-06 

7.389951992038948e-07 7.586308124398117e-06
2.906939113706309e-07 8.02865082863176e-06
2.2751229238013112e-06 8.554424570473008e-06
1.2758009038530123e-06 8.992805573516744e-06
1.2758009038530123e-06 8.992805573516744e-06
1.2611230230221826e-06 9.742786140156225e-06
1.5437527240577907e-06 9.59177102665226e-06
0.005559830523819708 1.301909009525456e-05
4.0789431912421466e-07 9.040434129561736e-06
0.008970073139884474 1.3180337742884603e-05
5.638761583350818e-07 8.060421592994372e-06
6.737017013047728e-07 8.2071920631533e-06
4.5069504838649734e-07 7.3801058861139745e-06
1.1423959092295321e-06 9.112490408694775e-06
1.1423959092295321e-06 9.112490408694775e-06
1.1423959092295321e-06 9.112490408694775e-06
1.1423959092295321e-06 9.112490408694775e-06
1.3013460098749252e-06 9.440725953717087e-06
7.112439506818967e-07 7.827521894970733e-06
0.00483833663882337 1.3010014385862836e-05
1.2571311405986533e-06 9.596023442321278e-06
1.298506808405963e-06 9.315234396370623e-06
1.301735302912154e-06 9.

## Zadanie 2 Page Rank

In [131]:
# the same as above but with different matrix

# power iterations method
def pagerank(A, G, e, max_iter: int = 1000, epsilon: float = 10**-14) -> Tuple[np.float64, np.ndarray]:
    n: int = A.get_shape()[0]
    result: np.ndarray = np.ones(n)
    prev_result:np.ndarray = np.zeros(n)
    dominant_eigenvalue: float = 0
        
    iter_count = 0
    while iter_count < max_iter and np.linalg.norm(prev_result - result) > epsilon:
        prev_result = result
        result = result @ A
        d = np.linalg.norm(prev_result) - np.linalg.norm(result)
        result = result + d * e
        dominant_eigenvalue = np.abs(sparse.find(result)[2]).max()
        result = result / dominant_eigenvalue
        iter_count += 1 
        
    return dict(zip(list(G), map(float, result)))

In [132]:
n = adj_matrix.get_shape()[0]
e = np.full(n, 1 / n)

custom_pagerank = pagerank(adj_matrix , graph, e)

In [133]:
for el1, el2 in [ tuple([custom_pagerank[i], lib_pagerank[i]]) for i in custom_pagerank.keys()]:
    print(el1, el2)

0.00013119510517307974 0.0001784471251795752
8.444299884191847e-05 9.82354842394754e-05
3.266252247970088e-05 3.5294288543868755e-05
6.529517025548387e-05 7.944147299221839e-05
5.77202872885925e-05 7.16916429079427e-05
3.4654771836061114e-06 7.056331940857706e-06
5.554101416785787e-05 6.710372514979558e-05
1.3623053988317416e-05 2.05819785531596e-05
0.00020088343517966832 0.00022648446678898572
3.5087964020037837e-06 9.555011146194654e-06
3.1494776639420906e-05 4.0626049225873195e-05
1.804582821570339e-05 2.921943424802018e-05
4.029634182859132e-05 5.7577387020891234e-05
5.2969463959235696e-05 7.112815808882015e-05
9.072760505378514e-05 0.00011703728383908945
0.0003257441551350262 0.0004938977049512389
9.727163577849017e-06 1.5269928612590688e-05
0.00010554804900210153 0.00012149823469656375
1.175301064918621e-05 2.1181024681375094e-05
6.160741432519601e-05 6.97597948022706e-05
9.28841327615891e-05 0.00011364069457463572
2.4672225105673183e-05 3.281564720529894e-05
0.000138957348193260

2.927219856999977e-06 1.338296154479668e-05
2.965265444116184e-06 5.461668401797866e-06
0.00012657010014192438 0.00018225510587582225
1.1934677920003815e-06 5.38239995156553e-06
5.237661594492886e-06 8.686865948169317e-06
1.816661952413061e-05 2.982503136321198e-05
2.8914036786869816e-05 3.661768910573748e-05
5.259133685938535e-06 7.65932180611712e-06
3.0484516581729064e-06 7.084849235406381e-06
3.2470088375467837e-06 6.762935512511373e-06
1.4032366822694486e-05 2.3122685370864503e-05
2.9732299016241694e-06 6.0398642182105216e-06
4.4715500115321685e-06 1.4288440263628002e-05
7.139501214925612e-06 1.0922840091627861e-05
5.6191835701804183e-05 7.432409383646158e-05
3.955984373985171e-06 7.44871059041299e-06
4.689479690433041e-06 1.074831701961842e-05
4.732789909853802e-06 7.711752322548325e-06
1.7851753046437553e-06 4.790455799259306e-06
2.7645148673754272e-06 5.347559373949018e-06
8.668973054803713e-06 1.6601841257356646e-05
2.798769746627045e-06 5.392061619578974e-06
9.718586481458894e

2.7567531877167005e-06 5.915596052416529e-06
4.4305612072631706e-06 8.061019423508967e-06
1.0338913071885658e-05 1.6129760232254882e-05
2.7914946951783803e-06 1.0888076115043769e-05
1.1377013570113385e-06 5.686389559280653e-06
1.0167941369260974e-05 1.5494089731674176e-05
2.698349445487417e-05 3.8922669996294045e-05
3.2520842262210217e-06 7.53234850998146e-06
1.1377013570113385e-06 5.686389559280653e-06
6.7750935378088185e-06 1.0888092117171489e-05
6.610527690608124e-06 1.0184261471037658e-05
8.749621261322013e-06 1.330195073892785e-05
1.722853897269023e-06 5.27507842760668e-06
8.014959655998813e-06 1.1499676013732165e-05
2.7836888298922325e-06 6.395852586042787e-06
3.181571286636961e-05 4.231454977076769e-05
3.7770667391203595e-06 7.396930034134161e-06
1.561423155800285e-06 4.957030535430331e-06
1.1377013570113385e-06 5.686389559280653e-06
1.1377013570113385e-06 5.686389559280653e-06
5.0074451376578565e-05 6.582643094670547e-05
1.4384527063854653e-06 6.585969328321423e-06
8.5069620898

1.0663892183470514e-05 1.588968409693887e-05
1.1300209506226991e-05 1.6258778534510415e-05
3.489989255581073e-05 5.303356430911574e-05
4.6212432494057106e-06 9.424098203989764e-06
1.949000546442161e-06 1.0398997041137543e-05
5.585531453575688e-05 7.069679520472148e-05
0.00014177465632216608 0.00024456317076792844
1.2107009895050815e-05 1.4243868419134286e-05
3.0327876400132007e-05 4.209508340589103e-05
1.6018908742032767e-06 4.359653527012639e-06
0.0001178760362342217 0.00015210617083285456
1.95130516620069e-05 2.453713931451179e-05
1.207729185326815e-05 1.6788554854388915e-05
3.375925514412824e-05 4.4218118887317514e-05
6.564158988252427e-05 9.330584426460948e-05
4.53404131120688e-05 6.40021179020899e-05
4.9878311456587374e-05 6.733353090856495e-05
1.3758720045968038e-05 1.694382136780055e-05
0.00011119962039553549 0.00013519877005837338
8.493754192787302e-05 9.97047799997467e-05
3.3037118831942146e-05 4.4571972860771947e-05
1.2657469816265152e-05 1.5624606958299093e-05
6.588238375169

2.8929802009564968e-05 4.17310908408805e-05
5.214552038547681e-05 5.0556695496878075e-05
1.3216833083375029e-05 1.6614153236292908e-05
3.400496426394502e-05 4.427185636196899e-05
3.092934324399185e-05 3.9709824808791696e-05
5.4822021488948375e-05 4.1241621973383645e-05
1.0139708471883e-05 8.705114189784309e-06
0.00010010901229475563 0.00010754440777182118
9.730186221575621e-05 0.00012058533896052731
1.6599311457300992e-06 3.9919428716965e-06
7.536842568146721e-06 1.232605530837137e-05
2.85037777199804e-05 3.2222109484511115e-05
5.9549841206814894e-05 8.227797084921703e-05
2.4428450929298247e-06 4.743867021415626e-06
1.0230749432921473e-05 1.8421526652758694e-05
1.4187114400654744e-05 2.4596260252539432e-05
5.730591974331532e-05 5.2606575498234135e-05
2.4092034186614896e-05 2.7631750888640793e-05
4.104422766850866e-06 6.7568542260831535e-06
4.022078295163343e-06 1.3060172294669068e-05
8.25967741888538e-05 0.0001169316413506103
1.7355600573307986e-06 4.047736262597658e-06
8.1880130254901

...

1.0832461787805755e-06 7.419032346603309e-06
1.4898630744141115e-06 6.860256008322306e-06
8.555645285348021e-07 6.786119189850761e-06
1.963833606439344e-06 8.219926072060163e-06
1.2433417443683243e-06 5.944603326230525e-06
3.265663399444322e-06 8.00408671579377e-06
1.2709711594746553e-06 7.351928569446891e-06
1.2709711594746553e-06 7.351928569446891e-06
1.262282097567309e-06 5.502878445710415e-06
2.366559763885714e-06 5.381281592430285e-06
0.01909441743057897 1.382697550133125e-05
0.01909441743057897 1.382697550133125e-05
0.01909441743057897 1.382697550133125e-05
6.662601632330637e-07 5.073810673749133e-06
5.905407307974072e-07 6.4739282182592e-06
5.905407307974072e-07 6.4739282182592e-06
1.1851645996735023e-06 5.749874031520059e-06
1.2103158087511118e-06 6.373889655253394e-06
1.3252666116962896e-06 9.171607939102272e-06
1.2533367129858037e-06 5.729511564703541e-06
1.1915290716968826e-06 5.551563640702411e-06
1.1915290716968826e-06 5.551563640702411e-06
1.1915290716968826e-06 5.5515636

1.1822245975718974e-06 6.425802364016435e-06
9.737927224854502e-07 5.042686099137041e-06
1.3417541333748e-06 5.715747660784571e-06
1.2665970661045688e-06 5.520128349846556e-06
1.1522914095428137e-06 6.837172018217007e-06
1.389133155308848e-06 6.476971138619945e-06
3.326865168413088e-06 1.1037972026225904e-05
1.3252135871220287e-06 7.792926123241296e-06
1.4507190711324988e-06 9.148626042660522e-06
1.215526189829673e-06 6.689494748440597e-06
1.3731536408082647e-06 5.384648587972361e-06
0.011980776125228758 1.3389845614572918e-05
5.7276379986074e-07 6.4782010135854084e-06
5.7276379986074e-07 6.4782010135854084e-06
1.7430172906509295e-06 9.312589767462141e-06
1.2261151328093015e-06 5.582798682088449e-06
1.2261151328093015e-06 5.582798682088449e-06
1.927440035736608e-06 8.283153502058905e-06
1.508596485547628e-06 5.833354472512491e-06
0.03885240860385291 1.551496212446228e-05
0.04103678211282085 1.5395633021393646e-05
1.5583821407783604e-06 5.799336687345892e-06
1.396677580924897e-06 8.1715

0.010321385459168872 1.3249074252714986e-05
0.01622801366005265 1.3539054029413076e-05
0.010321385459168872 1.3249074252714986e-05
0.010321385459168872 1.3249074252714986e-05
0.010321385459168872 1.3249074252714986e-05
0.010321385459168872 1.3249074252714986e-05
0.010321385459168872 1.3249074252714986e-05
0.010321385459168872 1.3249074252714986e-05
9.283005365310989e-07 6.230713510700096e-06
1.564913528006331e-06 9.287493108596266e-06
3.8057231589383225e-06 9.912516872137873e-06
1.3635380244922376e-06 7.382738251757655e-06
1.0701813601612497e-06 6.528227659134104e-06
1.2509775151833873e-06 9.25880804652942e-06
1.7697886828486307e-06 1.2979357450116517e-05
1.1385275017316045e-06 9.022682350871784e-06
7.640043377642368e-07 5.306738286121512e-06
1.1967247412423401e-06 8.427549919646276e-06
2.1658547551335248e-06 6.907072902370845e-06
1.4931715328201524e-06 7.692677509839774e-06
9.0274744070773e-07 6.115951285845921e-06
1.2109658188975132e-06 6.33352054591189e-06
1.2109658188975132e-06 6.3

1.2350157555143029e-06 9.161357319778957e-06
1.2195183030325086e-06 7.115745015861046e-06
1.834242558589156e-06 9.63675282138389e-06
1.154105310845113e-06 6.5781449640668875e-06
1.3904614374356498e-06 9.194251028030431e-06
1.4500054821149882e-06 9.056574625430027e-06
2.0690604012509492e-06 7.054276123681607e-06
1.0187581404555761e-06 6.834261653188725e-06
1.9603328902116216e-06 9.357820350547521e-06
6.613425213434342e-07 5.268651376795268e-06
1.1256179256442518e-06 9.119209629884102e-06
1.0070252803480552e-06 9.306337640164275e-06
1.1062238443466033e-06 9.25958273836577e-06
8.328153720765374e-07 6.893400025183373e-06
1.3837591928030325e-06 1.1953637788774527e-05
1.1649104316962565e-06 7.592187111158867e-06
1.2524878561400267e-06 5.987888649117346e-06
3.882649663818359e-06 1.4152513601057072e-05
2.2466353933123173e-06 1.0998910873782842e-05
1.7951438696860702e-06 8.99403361331897e-06
2.2466353933123173e-06 1.0998910873782842e-05
7.747150309121113e-07 4.933574970513068e-06
1.795143869686

2.3599966273762537e-06 9.76389748637833e-06
1.2481905921899754e-06 1.0367921419110303e-05
1.1074386865508983e-06 9.60017215960739e-06
2.5041596109165882e-06 1.3580625092175069e-05
2.483890128173792e-06 1.1538430010615772e-05
1.6458832204340412e-06 8.892947635567331e-06
2.483890128173792e-06 1.1538430010615772e-05
1.6458832204340412e-06 8.892947635567331e-06
9.632524736435757e-07 9.681103467709892e-06
1.0979966078931888e-06 9.966805842504146e-06
8.555039953211616e-07 1.0393732643447844e-05
2.607938795707278e-06 1.447225091717061e-05
0.0705198107327259 2.1376459699277573e-05
9.322969742116346e-07 9.969552712543706e-06
2.963183718816426e-06 1.17270218304566e-05
2.963183718816426e-06 1.17270218304566e-05
0.006684860888498384 1.1673799308350551e-05
1.2783640459815573e-06 9.76816267125535e-06
1.0915369496438633e-06 9.852251934879224e-06
9.915239119224015e-07 9.362643140116704e-06
1.7407106135916474e-06 1.0033080028835147e-05
1.040899931040719e-06 9.534746509713646e-06
3.095557844497106e-06 1